## Assignment 7

### Seismometer transfer function and correlation

In [ ]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
from setupFigure import SetupFigure
from dftFast import dft_fast_coeff, dft_fast_synthesis
from seismicTrace import SeismicTrace

#### Task 1: Write a function that calculates the transfer function of a seismometer for different damping $h=\sin\phi$.

In [ ]:
def transfer_seismometer_velocity(fc, df, nf, phi, sigma):
    """
    Calculates samples of the ground velocity seismometer transfer function (positive frequencies only)
    :param fc: eigenfrequency of seismometer in Hz
    :param df: frequency stepping
    :param nf: number of frequencies
    :param phi: damping angle in degrees (h=sin(phi))
    :param sigma: generator constant
    :return array with frequencies, array of complex values of transfer function
    """
    f = df*np.arange(0, nf)
    alfa = np.deg2rad(phi)
    return f, -sigma*(f/fc)/(f/fc-np.exp(1j*alfa)) * (f/fc)/(f/fc-np.exp(1j*(np.pi-alfa)))

#### You may use this function for the Butterworth lowpass filter (or your own from Assignment 6)

In [ ]:
def butterworth_lowpass(fc, df, nf, order):
    """
    Calculates samples of the lowpass Butterworth filter transfer function (positive frequencies only)
    :param fc: corner frequency in Hz
    :param df: frequency stepping in Hz
    :param nf: number of frequencies
    :param order: filter order
    """
    f = df*np.arange(0, nf)
    h = np.ones(nf, dtype=np.complex64)
    for k in range(order):
        arg = 1j*(2*k+1)*np.pi/(2*order)
        h = h*(-1j)/(f/fc-np.exp(arg))
    return h

#### This is a useful function to plot traces next to each other with a vertical offset

In [ ]:
def plotTraceGather(tracelist, ax):
    """
    Plots a gather of traces with vertical offset
    :param tracelist: list of SeismicTrace objects
    :param ax: Matplotlib axis object
    """
    for j, tr in enumerate(tracelist):
        t = tr.tanf+tr.dt*np.arange(0, tr.nsamp)
        norm = np.max(np.abs(tr.vals))
        ax.plot(t, 0.5*tr.vals/norm+j, color='b', ls='-')   # Normalization to 0.5*absmax and shift by multiples of 1
        ax.text(tr.tanf, j+0.1, tr.staname, fontsize=14)    # Add station name on top of trace

#### Task 2.1: Write a function that computes the cross correlation function for a given range of time delays

In [ ]:
def crossCorrelation(x, y, dt, neglim, poslim):
    """
    Correlate x with y according to c_n = Delta t*sum_(k=0)^(N-1) x_(n+k) y_k.
    Assumes that both traces have same DT!
    Consider x is a Gaussian with max at t2, y a Gaussian with max at t1 < t2.
    To bring x and y into a match, x neeeds to be shifted to the left implying a positive n=n_s.
    Thus, ns*dt is the delay of x relative to y or the advance of y relative to x.
    If n+k < 0 or n+k >= x.size, x_(n+k) is considered as zero.
    :param x: values of first trace
    :param y: values of second trace
    :param dt: sampling interval
    :param neglim: most negative value for n
    :param poslim: most positive value for n (poslim not included)
    :return: array of delay times associated with the array elements of the cross correlation
    :return: array of values of the cross correlation function
    """
    nsamp = poslim-neglim
    cc = np.zeros(nsamp)
    for n in range(neglim, poslim):
        nc = n-neglim                  # adjust index associating index 0 to neglim
        for k in range(y.size):
            if n+k >= 0 and n+k < x.size:
                cc[nc] = cc[nc]+x[n+k]*y[k]
    return dt*np.arange(neglim, poslim), cc*dt

#### Task 2.2: Evaluate the amplitude spectrum of the seismometer transfer function for different angles
Use fc = 10 Hz, nf = 256, df = 0.2, sigma = 1. Choose angles 15, 25, 45, 60, 85 degrees. Plot the
amplitude spectra into one graph.

In [ ]:
fc = 10
nf = 256
df = 0.2
sigma = 1
phi = [15, 25, 45, 60, 85]
col = ['black', 'red', 'blue', 'orange', 'magenta']

In [ ]:
fig1, ax1 = SetupFigure(12, 5, "Frequency [Hz]", "$|H(f)|$", "Amplitude of seismometer transfer function", 14)
for j, p in enumerate(phi):
    f, hseis = transfer_seismometer_velocity(fc, df, nf, p, sigma)
    ax1.plot(f, np.absolute(hseis), color=col[j], ls='-', label="Phi = {:4.0f}".format(p))
ax1.legend()

#### Task 2.3: Evaluate the phase spectrum of the seismometer transfer function for different angles
Use fc = 10 Hz, nf = 256, df = 0.2, sigma = 1. Choose angles 15, 25, 45, 60, 85 degrees. Plot the
amplitude spectra into one graph.

In [ ]:
fig2, ax2 = SetupFigure(12, 5, "Frequency [Hz]", "Phase / PI", "Phase of seismometer transfer function", 14)
for j, p in enumerate(phi):
    f, hseis = transfer_seismometer_velocity(fc, df, nf, p, sigma)
    ax2.plot(f, np.angle(hseis)/np.pi, color=col[j], ls='-', label="Phi = {:4.0f}".format(p))
ax2.legend()

#### Task 2.4: Setup two Gaussians $e^{-(t-\mu)^2/\sigma^2}$ of lengths 100 s and 80 s with dt=1 s, $\mu$=45 and 55 and $\sigma$ = 5. Plot the two into one graph. Then, compute the cross correlation between -30 and +30 s using your function from Task 2 and plot it into a separate graph. 

In [ ]:
tx = np.arange(0,100)
ty = np.arange(0,80)
x = np.exp(-((tx-45)/5)**2)
y = np.exp(-((ty-55)/5)**2)
fig7, ax7 = SetupFigure(12, 5, "Time [s]", "Amplitude", "Two Gaussians", 14)
ax7.plot(tx, x, color='blue', ls='-', label='Time series x(t)')
ax7.plot(ty, y, color='red', ls='-', label='Time series y(t)')
ax7.legend()

In [ ]:
tc, cc = crossCorrelation(x, y, 1.0, -30, 30)
fig8, ax8 = SetupFigure(12, 5, "Time delay [s]", "Correlation", "Cross correlation", 14)
ax8.plot(tc, cc, color='blue', ls='-')

#### Task 2.5: For comparison, use numpy's routine correlate to calculate the correlation. Try the different modes offered.
Change the lengths of x and y.

In [ ]:
fig9, ax9 = SetupFigure(12, 5, "Time delay [s]", "Correlation", "Numpy cross correlation", 14)
ccnp = np.correlate(x, y, mode='full')
tcnp = np.arange(-y.size+1, x.size)    # This seems to be the correct relation between lag and index
print(x.size, y.size)
ax9.set_xlim(-30,30)
ax9.plot(tcnp, ccnp, color='red', ls='-')

#### Task 3.1: We want to prepare time delay measurements between two seismograms by cross-correlation. First, read the data of stations CH.PANIX and Z3.A261A.HHZ. Put the SeismicTrace objects into a list.

In [ ]:
stalist = ["CH.PANIX.HHZ", "Z3.A261A.HHZ"]
rawlist = []
for sta in stalist:
    with open(sta, 'r') as fd:
        tr = SeismicTrace.readFromAscii(fd)
    tr.printInfo()
    rawlist.append(tr)

#### Task 3.2: Plot the traces using the function plotTraceGather.

In [ ]:
fig3, ax3 = SetupFigure(12, 5, "Time [s]", "Displacement", "Raw traces", 14)
plotTraceGather(rawlist, ax3)

#### Task 3.3: Filter the data using a Butterworth low pass with fc=0.5 Hz and order 6. Use either the provided function for the low-pass transfer function or take your own. First, Fourier transform the data, then multiply with the filter transfer function, and finally do the back transform. Create new SeismicTrace objects for the filtered traces, put them into a list and plot them.

In [ ]:
fc = 0.5; order = 6
filtlist = []
for tr in rawlist:
    c = dft_fast_coeff(tr.vals)
    df = 1./tr.tlen
    hb = butterworth_lowpass(fc, df, c.size, order)
    fts = c*hb
    s = dft_fast_synthesis(fts, outnum='even')
    trfil = SeismicTrace(tr.staname, tr.comp, tr.dt, tr.tanf, s)
    filtlist.append(trfil)

In [ ]:
fig4, ax4 = SetupFigure(12, 5, "Time [s]", "Displacement", "Low pass filtered traces, fc = {:5.2f} Hz, Order = {:d}".format(fc, order), 14)
plotTraceGather(filtlist, ax4)

In [ ]:
winlist = [[64285, 64300], [64280, 64295.1]]
cutlist = []
for j, tr in enumerate(filtlist):
    win = winlist[j]
    jfirst = int((win[0]-tr.tanf)/tr.dt)
    jlast = int((win[1]-tr.tanf)/tr.dt)
    nsamp = jlast-jfirst
    tanew = jfirst*tr.dt+tr.tanf
    print(tr.tanf, tanew, jfirst, jlast)
    cuttr = SeismicTrace(tr.staname, tr.comp, tr.dt, tanew, tr.vals[jfirst:jlast])
    cutlist.append(cuttr)

In [ ]:
fig5, ax5 = SetupFigure(12, 5, "Time [s]", "Displacement", "Cut low pass filtered traces".format(fc, order), 14)
plotTraceGather(cutlist, ax5)

In [ ]:
dt = cutlist[0].dt
neglim = -500; poslim = 500
t, cc = crossCorrelation(cutlist[0].vals, cutlist[1].vals, dt, neglim, poslim)
delay = (np.argmax(cc)+neglim)*dt+cutlist[0].tanf-cutlist[1].tanf
print("Tanf_0 = ", cutlist[0].tanf, "Tanf_1 = ", cutlist[1].tanf, "Index of max cc: ", np.argmax(cc)+neglim)
print("Delay of ", cutlist[0].staname," relative to ", cutlist[1].staname,":", delay)

In [ ]:
fig6, ax6 = SetupFigure(12, 5, "Time delay [s]", "Correlation", "Cross correlation", 14)
ax6.plot(t, cc, color='blue', ls='-')